# 0. Initialisation

## 0.1 Imports

In [160]:
import pandas as pd
import numpy as np
from collections import Counter
import chardet
import editdistance #
import jellyfish
import re
from tqdm import tqdm
import os
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity

#DATA_PATH = r"C:\Users\Louis\Documents\University\Masters\A23\NLP\Devoirs\data\hw2"
DATA_PATH = r"C:\Users\barka\Desktop\NLP"

C:\Users\barka\anaconda3\lib\site-packages\scipy\__init__.py:155: UserWarning: A NumPy version >=1.18.5 and <1.25.0 is required for this version of SciPy (detected version 1.26.0
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


## 0.2 Functions

In [161]:
def detect_encoding(file_path):

    with open(file_path, 'rb') as file:
        rawdata = file.read()
    result = chardet.detect(rawdata)
    return result['encoding']

def get_word_counter(file_path, encoding):
    word_counter = Counter()

    with open(file_path, 'r', encoding=encoding) as file:
        for line in file:
            parts = line.split()
            if len(parts) >= 2:
                word = parts[1]
                count = int(parts[0]) 
                word_counter[word.strip()] = count

    return word_counter


def build_unigram_model(word_counter):
    unigram_model = {}

    total_words = sum(word_counter.values())

    for word, count in word_counter.items():
        probability = count / total_words

        unigram_model[word] = probability

    return unigram_model

## 0.3 Check data quality
Make sure Python is reading the lines correctly. And it does!

In [162]:
# Check ypos
typos_file = open(DATA_PATH + r"\typo-0.2.txt")

for i, row in enumerate(typos_file):
    #print(row)
    pass

print(f"There are {i+1} rows in the file. There should be 1000. Correct number? {i+1==1000}")

# Check vocabulary

encoding = detect_encoding(DATA_PATH + r"\voc-1bwc.txt") #check encoding
print(f"Encoding : {encoding}")

voc = open(DATA_PATH + r"\voc-1bwc.txt", encoding=encoding)

for i, row in enumerate(voc):
    #print(row)
    pass


There are 1000 rows in the file. There should be 1000. Correct number? True


Encoding : utf-8
There are 201315 rows in the file. There should be 201 315. Correct number? True


How many words in the vocabulary?

In [163]:
vocab = get_word_counter(DATA_PATH + r"\voc-1bwc.txt", encoding)
print(len(vocab)) # just to verify

202971


In [164]:
vocab["the"]

41640816

In [165]:
unigram_model = build_unigram_model(vocab)

In [166]:
unigram_model["the"]

0.06258941042979899

# 1. Implementing various distances

### 1.1 Generic Distance function

Works with any function that takes two words as an input. 

In [167]:
'''This function applies a generic function over an entire vocabulary to compare the distance between a given word
and every word inside the vocabulary. It then returns the n_neighbors most similar words.

Parameters:
    word: The word to find neighbors to.
    vocabulary: A list (or list-like) of the vocabulary.
    func: The distance function to apply without arguments (without parentheses).
    minimum: Do we want the minimum distance? Boolean. True by default, will yield the minimum distance. If False, the function will yield the maximum distance. 
    n_neighbors: The number of most similar words to return.

Returns:
    vocabulary.head: A dataframe containing the n_neighbors most similar words to the input word, with the distances. 
'''
def generic_distance_correction(word, vocabulary, func, minimum = True, n_neighbors=1):
    vocabulary = pd.DataFrame(vocabulary, columns=["words"])

    def calculateDistance(series_word):
        return func(series_word, word)
    
    distances = vocabulary["words"].apply(calculateDistance)
    
    vocabulary["distance"] = distances

    vocabulary = vocabulary.sort_values("distance", ascending=minimum)

    return vocabulary.head(n_neighbors)

### Weighted Functions

In [233]:
def edDistance_unigram_correction(word, vocabulary, n_neighbors=1):
    vocabulary = pd.DataFrame(vocabulary, columns=["words"])

    def calculateDistance(series_word):
        return editdistance.eval(series_word, word)
    
    def unigram_weighing(word):
        return unigram_model[word]

    distances = vocabulary["words"].apply(calculateDistance)
    vocabulary["distance"] = distances
    vocabulary["weight"] = vocabulary["words"].apply(unigram_weighing)

    vocabulary = vocabulary.sort_values(["distance", "weight"], ascending=[True, False])

    return vocabulary.head(n_neighbors)

def edDistance_soundex_correction(word, vocabulary, n_neighbors=1):
    vocabulary = pd.DataFrame(vocabulary, columns=["words"])

    def calculateDistance(series_word):
        return editdistance.eval(series_word, word)
    
    distances = vocabulary["words"].apply(calculateDistance)
    vocabulary["distance"] = distances
    vocabulary = vocabulary.sort_values("distance", ascending=True)
    
    # Then, out of the head, sort by soundex
    top_words = vocabulary.head(n_neighbors)
    soundex = []
    word_sdx = jellyfish.soundex(word)
    for word in top_words["words"]:
        corr_sdx = jellyfish.soundex(word)
        sdx_ed_distance = editdistance.eval(word_sdx, corr_sdx)
        soundex.append(sdx_ed_distance)
    top_words["soundex"] = soundex
    top_words = top_words.sort_values(["distance", "soundex"], ascending=[True, True])

    return top_words

def edDistance_composite_correction(word, vocabulary, alpha=0.5, n_neighbors=1):
    vocabulary = pd.DataFrame(vocabulary, columns=["words"])

    def calculateDistance(series_word):
        return editdistance.eval(series_word, word)
    
    def unigram_weighing(word):
        return unigram_model[word]

    distances = vocabulary["words"].apply(calculateDistance)
    vocabulary["distance"] = distances

    vocabulary = vocabulary.sort_values("distance", ascending=True)

    top_words = vocabulary.head(n_neighbors)
    soundex = []
    word_sdx = jellyfish.soundex(word)
    for word in top_words["words"]:
        corr_sdx = jellyfish.soundex(word)
        sdx_ed_distance = editdistance.eval(word_sdx, corr_sdx)
        soundex.append(sdx_ed_distance)
    top_words["soundex"] = soundex
    top_words["weight"] = top_words["words"].apply(unigram_weighing)
    top_words["weight"] = top_words["weight"] / top_words["weight"].sum()

    top_words["composite_weight"] = alpha * (1 - top_words["weight"]) + (1-alpha) * top_words["soundex"]
    top_words = top_words.sort_values(["distance", "composite_weight"], ascending=[True, True])

    return top_words

In [234]:
def numeric_unigram_correction(word, vocabulary, func, n_neighbors=1):
    vocabulary = pd.DataFrame(vocabulary, columns=["words"])

    def calculateDistance(series_word):
        return func(series_word, word)
    
    def unigram_weighing(word):
        return unigram_model[word]

    distances = vocabulary["words"].apply(calculateDistance)
    vocabulary["distance"] = distances

    # Sort the values using the weight and only keep the head
    top_words = vocabulary.sort_values("distance", ascending=False).head(n_neighbors)

    # Make the weights relative to each other, using only the top words
    top_words["weight"] = top_words["words"].apply(unigram_weighing)
    top_words["weight"] = top_words["weight"] / top_words["weight"].sum()

    # Weight the distance
    top_words["wgt_distance"] = top_words["distance"] * top_words["weight"]

    # Sort the top words using the weighted distance
    top_words = top_words.sort_values("wgt_distance", ascending=False)

    return top_words

def numeric_soundex_correction(word, vocabulary, func, n_neighbors=1):
    vocabulary = pd.DataFrame(vocabulary, columns=["words"])

    def calculateDistance(series_word):
        return func(series_word, word)
    
    distances = vocabulary["words"].apply(calculateDistance)
    vocabulary["distance"] = distances
    vocabulary = vocabulary.sort_values("distance", ascending=False)
    
    # Then, out of the head, sort by soundex
    top_words = vocabulary.head(n_neighbors)
    soundex = []
    word_sdx = jellyfish.soundex(word)
    for word in top_words["words"]:
        corr_sdx = jellyfish.soundex(word)
        sdx_ed_distance = editdistance.eval(word_sdx, corr_sdx)
        soundex.append(sdx_ed_distance)
    top_words["soundex"] = 1 - soundex / np.sum(soundex)
    top_words["wgt_distance"] = top_words["distance"] * top_words["soundex"]
    
    top_words = top_words.sort_values("wgt_distance", ascending=False)

    return top_words

def numeric_composite_correction(word, vocabulary, func, alpha = 0.5,  n_neighbors=1):
    vocabulary = pd.DataFrame(vocabulary, columns=["words"])

    def calculateDistance(series_word):
        return func(series_word, word)

    def unigram_weighing(word):
        return unigram_model[word]
    
    distances = vocabulary["words"].apply(calculateDistance)
    vocabulary["distance"] = distances
    vocabulary = vocabulary.sort_values("distance", ascending=False)
    
    # Then, out of the head, sort by soundex
    top_words = vocabulary.head(n_neighbors)
    soundex = []
    word_sdx = jellyfish.soundex(word)
    for word in top_words["words"]:
        corr_sdx = jellyfish.soundex(word)
        sdx_ed_distance = editdistance.eval(word_sdx, corr_sdx)
        soundex.append(sdx_ed_distance)
    top_words["soundex"] = 1 - soundex / np.sum(soundex)
    
    # Make the weights relative to each other, using only the top words
    top_words["weight"] = top_words["words"].apply(unigram_weighing)
    top_words["weight"] = top_words["weight"] / top_words["weight"].sum()

    # Weight the distance
    top_words["wgt_distance"] = top_words["distance"] *  (alpha * top_words["weight"] + (1-alpha) * top_words["soundex"])
    
    top_words = top_words.sort_values("wgt_distance", ascending=False)

    return top_words

### 1.2. Testing the correction methods

In [235]:
generic_distance_correction('speling', vocab.keys(), editdistance.eval, True, 5) #Edit distance

words  distance
172484  sperling         1
191321  spelling         1
179101   spewing         1
123329   spaying         2
187893   seeming         2

In [236]:
edDistance_unigram_correction("speling", vocab.keys(), 5)

words  distance    weight
191321  spelling         1  0.000005
179101   spewing         1  0.000002
172484  sperling         1  0.000001
202398  spending         2  0.000200
202060   opening         2  0.000131

In [237]:
edDistance_soundex_correction("speling", vocab.keys(), 5)

C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\1974657764.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["soundex"] = soundex


words  distance  soundex
191321  spelling         1        0
172484  sperling         1        2
179101   spewing         1        2
123329   spaying         2        2
187893   seeming         2        3

In [238]:
edDistance_composite_correction("speling", vocab.keys(), 0.5, 5)

C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\1974657764.py:62: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["soundex"] = soundex
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\1974657764.py:63: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["weight"] = top_words["words"].apply(unigram_weighing)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\1974657764.py:64: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,c

words  distance  soundex    weight  composite_weight
189762  spelling         1        0  0.429884          0.285058
177635   spewing         1        2  0.129028          1.435486
171215  sperling         1        2  0.083459          1.458270
185401  spilling         2        0  0.254909          0.372545
174478  smelling         2        1  0.102719          0.948640

In [212]:
generic_distance_correction('speling', vocab.keys(), jellyfish.jaro_similarity, False, 5)

words  distance
191321   spelling  0.958333
172484   sperling  0.958333
168457  spellings  0.925926
197912   sleeping  0.910714
187411      selig  0.904762

In [215]:
numeric_unigram_correction("speling", vocab.keys(), jellyfish.jaro_similarity, 5)

words  distance    weight  wgt_distance
197912   sleeping  0.910714  0.641903      0.584590
191321   spelling  0.958333  0.181914      0.174334
187411      selig  0.904762  0.113302      0.102511
172484   sperling  0.958333  0.035068      0.033607
168457  spellings  0.925926  0.027813      0.025753

In [216]:
numeric_soundex_correction("speling", vocab.keys(), jellyfish.jaro_similarity, 5)

C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\3621166141.py:46: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["soundex"] = 1 - soundex / np.sum(soundex)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\3621166141.py:47: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["wgt_distance"] = top_words["distance"] * top_words["soundex"]


words  distance   soundex  wgt_distance
191321   spelling  0.958333  1.000000      0.958333
168457  spellings  0.925926  1.000000      0.925926
172484   sperling  0.958333  0.714286      0.684524
197912   sleeping  0.910714  0.714286      0.650510
187411      selig  0.904762  0.571429      0.517007

In [226]:
numeric_composite_correction('speling', vocab.keys(), jellyfish.jaro_similarity, 0.5, 5)

C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["soundex"] = 1 - soundex / np.sum(soundex)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:77: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["weight"] = top_words["words"].apply(unigram_weighing)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:78: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try us

words  distance  soundex    weight  wgt_distance
189762   spelling  0.958333      1.0  0.203322      0.576592
196330   sleeping  0.910714      0.5  0.719100      0.555126
167278  spellings  0.925926      1.0  0.031436      0.477517
126688    sapling  0.904762      1.0  0.006668      0.455398
171215   sperling  0.958333      0.5  0.039474      0.258498

In [176]:
generic_distance_correction('speling', vocab.keys(), jellyfish.jaro_winkler_similarity, False, 5)

words  distance
191321   spelling  0.975000
172484   sperling  0.970833
168457  spellings  0.955556
179101    spewing  0.933333
197912   sleeping  0.919643

In [177]:
numeric_unigram_correction("speling", vocab.keys(), jellyfish.jaro_winkler_similarity, 5)

words  distance    weight  wgt_distance
197912   sleeping  0.919643  0.681877      0.627083
191321   spelling  0.975000  0.193242      0.188411
179101    spewing  0.933333  0.058084      0.054212
172484   sperling  0.970833  0.037252      0.036166
168457  spellings  0.955556  0.029545      0.028232

In [178]:
numeric_soundex_correction("speling", vocab.keys(), jellyfish.jaro_winkler_similarity, 5)

C:\Users\barka\AppData\Local\Temp\ipykernel_22968\1142548253.py:46: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["soundex"] = 1 - soundex / np.sum(soundex)
C:\Users\barka\AppData\Local\Temp\ipykernel_22968\1142548253.py:47: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["wgt_distance"] = top_words["distance"] * top_words["soundex"]


words  distance   soundex  wgt_distance
191321   spelling  0.975000  1.000000      0.975000
168457  spellings  0.955556  1.000000      0.955556
172484   sperling  0.970833  0.666667      0.647222
179101    spewing  0.933333  0.666667      0.622222
197912   sleeping  0.919643  0.666667      0.613095

In [227]:
numeric_composite_correction('speling', vocab.keys(), jellyfish.jaro_winkler_similarity, 0.5, 5)

C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["soundex"] = 1 - soundex / np.sum(soundex)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:77: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["weight"] = top_words["words"].apply(unigram_weighing)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:78: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try us

words  distance   soundex    weight  wgt_distance
196330   sleeping  0.919643  0.666667  0.682026      0.620158
189762   spelling  0.975000  1.000000  0.192840      0.581509
167278  spellings  0.955556  1.000000  0.029815      0.492023
171215   sperling  0.970833  0.666667  0.037439      0.341784
177635    spewing  0.933333  0.666667  0.057880      0.338122

## 1.3. Running the correction methods on the data

### 1.3.1 - Get the typos:

In [179]:
with open(DATA_PATH + r"\typo-0.2.txt", "r", encoding=encoding) as file:
    text = file.read()

typo_pattern = r'<typo orig="([^"]+)">([^<]+)</typo>'
typos = re.findall(typo_pattern, text)
typos = pd.DataFrame(typos, columns=["Word", "Typo"])


typos.tail(10)

Word          Typo
3173         defy         deefy
3174  translation  translatmion
3175           to           tho
3176          But            ut
3177           in           ini
3178         keep         kpeep
3179         game           gme
3180        winds       wantagh
3181         this           tsi
3182           of             o

In [180]:
s1 = set(typos["Word"])
s2 = set(vocab.keys())
inter = s2.intersection(s1)

print(f"There are {len(typos['Word'].unique())} unique original words and {len(pd.Series(vocab.keys()).unique())} unique words in the vocabulary. Out of these two, {len(inter)} intersect.")


There are 1601 unique original words and 202971 unique words in the vocabulary. Out of these two, 1279 intersect.


### 1.3.2 - Apply correction methods: 


In [239]:
def get_correction_df(path, typos, func, minimum = True, n_neighbors=1):

    if os.path.isfile(path):
        final_df = pd.read_csv(path, index_col = 0)

    else: 
        
        final_df = typos.copy()
        rows = pd.DataFrame() 

        for typo in tqdm(typos["Typo"].tolist(), desc="Correcting Typos", total=len(typos)):

            corrections = generic_distance_correction(typo, vocab.keys(), func, minimum, n_neighbors)

            new_row = corrections.transpose().reset_index(drop=True)
            new_row.columns = [str(i) for i in range(len(new_row.columns))]
            new_row = pd.concat([new_row.iloc[0], new_row.iloc[1]], axis=0).reset_index(drop=True)
            new_row = pd.DataFrame(new_row.values.flatten()).T 
            
            row = pd.DataFrame()
            for col in new_row.columns:
                if int(col) > 4 : 
                    row[f"distance {col-n_neighbors}"] = new_row[col]
                else: 
                    row[f"correction {col}"] = new_row[col]

            rows = pd.concat([rows, row], axis=0).reset_index(drop=True)

        final_df = pd.concat([final_df, rows], axis=1)

        final_df.to_csv(path)
    
    return final_df


def get_weighted_ed_correction_df(path, typos, unigram = True, n_neighbors=1):

    if os.path.isfile(path):
        final_df = pd.read_csv(path, index_col = 0)

    else: 
        
        final_df = typos.copy()
        rows = pd.DataFrame() 

        for typo in tqdm(typos["Typo"].tolist(), desc="Correcting Typos", total=len(typos)):
            
            if unigram:
                corrections = edDistance_unigram_correction(typo, vocab.keys(), n_neighbors)
            else:
                corrections = edDistance_soundex_correction(typo, vocab.keys(), n_neighbors)

            new_row = corrections.transpose().reset_index(drop=True)
            new_row.columns = [str(i) for i in range(len(new_row.columns))]
            new_row = pd.concat([new_row.iloc[0], new_row.iloc[3]], axis=0).reset_index(drop=True)
            new_row = pd.DataFrame(new_row.values.flatten()).T 
            
            row = pd.DataFrame()
            for col in new_row.columns:
                if int(col) > 4 : 
                    row[f"distance {col-n_neighbors}"] = new_row[col]
                else: 
                    row[f"correction {col}"] = new_row[col]

            rows = pd.concat([rows, row], axis=0).reset_index(drop=True)

        final_df = pd.concat([final_df, rows], axis=1)

        final_df.to_csv(path)
    
    return final_df

def get_composite_ed_correction_df(path, typos, alpha = 0.5, n_neighbors=1):

    if os.path.isfile(path):
        final_df = pd.read_csv(path, index_col = 0)

    else: 
        
        final_df = typos.copy()
        rows = pd.DataFrame() 

        for typo in tqdm(typos["Typo"].tolist(), desc="Correcting Typos", total=len(typos)):
            
            corrections = edDistance_composite_correction(typo, vocab.keys(), alpha, n_neighbors)
            
            new_row = corrections.transpose().reset_index(drop=True)
            new_row.columns = [str(i) for i in range(len(new_row.columns))]
            new_row = pd.concat([new_row.iloc[0], new_row.iloc[4]], axis=0).reset_index(drop=True)
            new_row = pd.DataFrame(new_row.values.flatten()).T 
            
            row = pd.DataFrame()
            for col in new_row.columns:
                if int(col) > 4 : 
                    row[f"weight {col-n_neighbors}"] = new_row[col]
                else: 
                    row[f"correction {col}"] = new_row[col]

            rows = pd.concat([rows, row], axis=0).reset_index(drop=True)

        final_df = pd.concat([final_df, rows], axis=1)

        final_df.to_csv(path)
    
    return final_df

def get_weighted_numeric_correction_df(path, typos, func, unigram = True, n_neighbors=1):

    if os.path.isfile(path):
        final_df = pd.read_csv(path, index_col = 0)

    else: 
        
        final_df = typos.copy()
        rows = pd.DataFrame() 

        for typo in tqdm(typos["Typo"].tolist(), desc="Correcting Typos", total=len(typos)):
            
            if unigram:
                corrections = numeric_unigram_correction(typo, vocab.keys(), func, n_neighbors)
            else:
                corrections = numeric_soundex_correction(typo, vocab.keys(), func, n_neighbors)

            new_row = corrections.transpose().reset_index(drop=True)
            new_row.columns = [str(i) for i in range(len(new_row.columns))]
            new_row = pd.concat([new_row.iloc[0], new_row.iloc[3]], axis=0).reset_index(drop=True)
            new_row = pd.DataFrame(new_row.values.flatten()).T 
            
            row = pd.DataFrame()
            for col in new_row.columns:
                if int(col) > 4 : 
                    row[f"distance {col-n_neighbors}"] = new_row[col]
                else: 
                    row[f"correction {col}"] = new_row[col]

            rows = pd.concat([rows, row], axis=0).reset_index(drop=True)

        final_df = pd.concat([final_df, rows], axis=1)

        final_df.to_csv(path)
    
    return final_df

def get_composite_numeric_correction_df(path, typos, func, alpha = 0.5, n_neighbors=1):

    if os.path.isfile(path):
        final_df = pd.read_csv(path, index_col = 0)

    else: 
        
        final_df = typos.copy()
        rows = pd.DataFrame() 

        for typo in tqdm(typos["Typo"].tolist(), desc="Correcting Typos", total=len(typos)):
            
            corrections = numeric_composite_correction(typo, vocab.keys(), func, alpha,  n_neighbors)
            
            new_row = corrections.transpose().reset_index(drop=True)
            new_row.columns = [str(i) for i in range(len(new_row.columns))]
            new_row = pd.concat([new_row.iloc[0], new_row.iloc[4]], axis=0).reset_index(drop=True)
            new_row = pd.DataFrame(new_row.values.flatten()).T 
            
            row = pd.DataFrame()
            for col in new_row.columns:
                if int(col) > 4 : 
                    row[f"distance {col-n_neighbors}"] = new_row[col]
                else: 
                    row[f"correction {col}"] = new_row[col]

            rows = pd.concat([rows, row], axis=0).reset_index(drop=True)

        final_df = pd.concat([final_df, rows], axis=1)

        final_df.to_csv(path)
    
    return final_df

**Jaro**

Took 9m21.8s on Louis' machine

In [182]:
jaro_correction_df = get_correction_df(DATA_PATH + "\jaro_correction_df.csv", typos, jellyfish.jaro_similarity, False, 5)
jaro_correction_df

Word             Typo correction 0  correction 1  correction 2  \
0      wealthy         wealtohy      wealthy        wealth         welty   
1       afford            aford       afford        axford        alford   
2     Catholic  CatholiaCtholic        athol  palaeolithic  pathological   
3      cousins         coxusins      cousins        cousin   compulsions   
4        masks           mmasks        masks          asks          mask   
...        ...              ...          ...           ...           ...   
3178      keep            kpeep         keep          peep        upkeep   
3179      game              gme          gme          gmes          gome   
3180     winds          wantagh      wantagh       wantage          wana   
3181      this              tsi          tsi          tsoi          tsim   
3182        of                o            o            og            op   

     correction 3 correction 4  distance 0  distance 1  distance 2  \
0         healthy       watley    0.958333    0.916667    0.875000   
1            ford      watford    0.944444    0.944444    0.944444   
2       alghaithi         atia    0.777778    0.766667    0.766667   
3            cusi     cosiness    0.958333    0.916667    0.837121   
4            mass      unmasks    0.944444    0.888889    0.888889   
...           ...          ...         ...         ...         ...   
3178        keeps        peeps    0.933333    0.933333    0.877778   
3179         game           gm    1.000000    0.916667    0.916667   
3180         anta         want    1.000000    0.904762    0.857143   
3181         gtsi         tsai    1.000000    0.916667    0.916667   
3182           oy           ox    1.000000    0.833333    0.833333   

      distance 3  distance 4  
0       0.869048    0.861111  
1       0.933333    0.904762  
2       0.765741    0.755556  
3       0.833333    0.833333  
4       0.888889    0.849206  
...          ...         ...  
3178    0.866667    0.866667  
3179    0.916667    0.888889  
3180    0.857143    0.857143  
3181    0.916667    0.916667  
3182    0.833333    0.833333  

[3183 rows x 12 columns]

Took 12mins

In [183]:
jaroUni_correction_df = get_weighted_numeric_correction_df(DATA_PATH + "\jaroUni_correction_df.csv", typos, jellyfish.jaro_similarity, True, 5)
jaroUni_correction_df

Word             Typo  correction 0 correction 1 correction 2  \
0      wealthy         wealtohy       healthy       wealth      wealthy   
1       afford            aford          ford       afford      watford   
2     Catholic  CatholiaCtholic  pathological        athol         atia   
3      cousins         coxusins        cousin      cousins  compulsions   
4        masks           mmasks          mass         asks         mask   
...        ...              ...           ...          ...          ...   
3178      keep            kpeep          keep        keeps       upkeep   
3179      game              gme          game           gm         gome   
3180     winds          wantagh          want         wana      wantage   
3181      this              tsi          tsai          tsi         gtsi   
3182        of                o             o           op           ox   

      correction 3 correction 4  distance 0  distance 1  distance 2  \
0           watley        welty    0.869048    0.916667    0.958333   
1           alford       axford    0.933333    0.944444    0.904762   
2     palaeolithic    alghaithi    0.766667    0.777778    0.755556   
3         cosiness         cusi    0.916667    0.958333    0.837121   
4            masks      unmasks    0.888889    0.888889    0.888889   
...            ...          ...         ...         ...         ...   
3178          peep        peeps    0.933333    0.866667    0.877778   
3179           gme         gmes    0.916667    0.888889    0.916667   
3180       wantagh         anta    0.857143    0.857143    0.904762   
3181          tsim         tsoi    0.916667    1.000000    0.916667   
3182            og           oy    1.000000    0.833333    0.833333   

      distance 3  distance 4  
0       0.861111    0.875000  
1       0.944444    0.944444  
2       0.766667    0.765741  
3       0.833333    0.833333  
4       0.944444    0.849206  
...          ...         ...  
3178    0.933333    0.866667  
3179    1.000000    0.916667  
3180    1.000000    0.857143  
3181    0.916667    0.916667  
3182    0.833333    0.833333  

[3183 rows x 12 columns]

Took 14m40.0s

In [184]:
jaroSdx_correction_df = get_weighted_numeric_correction_df(DATA_PATH + "\jaroSdx_correction_df.csv", typos, jellyfish.jaro_similarity, False, 5)
jaroSdx_correction_df

Word             Typo  correction 0 correction 1  correction 2  \
0      wealthy         wealtohy       wealthy       wealth         welty   
1       afford            aford        afford       alford        axford   
2     Catholic  CatholiaCtholic  pathological        athol  palaeolithic   
3      cousins         coxusins       cousins     coursing        cousin   
4        masks           mmasks         masks         mask          mass   
...        ...              ...           ...          ...           ...   
3178      keep            kpeep          keep          kpe          peep   
3179      game              gme           gme         game          gome   
3180     winds          wantagh       wantagh      wantage          want   
3181      this              tsi           tsi         tsoi          tasi   
3182        of                o           oco          ota           ofs   

     correction 3 correction 4  distance 0  distance 1  distance 2  \
0         healthy       watley    0.958333    0.916667    0.875000   
1            ford      watford    0.944444    0.755556    0.755556   
2       alghaithi         toit    0.702778    0.648148    0.575000   
3        coxswain  compulsions    0.766667    0.750000    0.733333   
4            asks      unmasks    0.944444    0.888889    0.888889   
...           ...          ...         ...         ...         ...   
3178        peeps       upkeep    0.829630    0.770370    0.725926   
3179         gmes        gamel    1.000000    0.916667    0.916667   
3180         anta         wata    1.000000    0.904762    0.714286   
3181         atsi         gtsi    1.000000    0.916667    0.916667   
3182          opt          otv    0.680556    0.680556    0.583333   

      distance 3  distance 4  
0       0.579365    0.287037  
1       0.653333    0.633333  
2       0.574306    0.566667  
3       0.666667    0.585985  
4       0.666667    0.212302  
...          ...         ...  
3178    0.674074    0.585185  
3179    0.458333    0.433333  
3180    0.571429    0.428571  
3181    0.458333    0.458333  
3182    0.583333    0.583333  

[3183 rows x 12 columns]

Took 38m20.7s

In [242]:
jaroCmp_correction_df = get_composite_numeric_correction_df(DATA_PATH + "\jaroCmp_correction_df.csv", typos, jellyfish.jaro_similarity, 0.5, 5)
jaroCmp_correction_df

Correcting Typos:   0%|          | 0/3183 [00:00<?, ?it/s]

C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["soundex"] = 1 - soundex / np.sum(soundex)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:77: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["weight"] = top_words["words"].apply(unigram_weighing)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:78: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try us

Word             Typo  correction 0 correction 1 correction 2  \
0      wealthy         wealtohy        wealth      wealthy      healthy   
1       afford            aford        afford         ford       alford   
2     Catholic  CatholiaCtholic  pathological         toit        athol   
3      cousins         coxusins        cousin      cousins     coursing   
4        masks           mmasks          mass        masks         mask   
...        ...              ...           ...          ...          ...   
3178      keep            kpeep          keep          kpe         peep   
3179      game              gme          game          gme         gome   
3180     winds          wantagh          want      wantagh      wantage   
3181      this              tsi           tsi         tsoi         tasi   
3182        of                o           opt          ota          oco   

      correction 3 correction 4 distance 0 distance 1 distance 2 distance 3  \
0            welty       watley   0.604697   0.588581   0.485506   0.437826   
1           axford      watford   0.658032   0.593786   0.380988    0.37796   
2     palaeolithic    alghaithi   0.572892   0.396475   0.346776   0.302743   
3         coxswain  compulsions   0.664722    0.52968   0.387464   0.336511   
4             asks      unmasks   0.744777   0.506714   0.479072    0.41023   
...            ...          ...        ...        ...        ...        ...   
3178         peeps       upkeep   0.876489   0.385614   0.364469   0.337807   
3179          gmes        gamel   0.915971   0.500077   0.458787   0.229207   
3180          anta         wata   0.785263   0.500102   0.452686    0.28575   
3181          gtsi         atsi   0.739234   0.504386   0.497807   0.347588   
3182           ofs          otv   0.654588   0.356442   0.346118   0.294482   

     distance 4  
0      0.143911  
1      0.328853  
2      0.296546  
3      0.295813  
4      0.106271  
...         ...  
3178   0.294658  
3179   0.216791  
3180   0.214325  
3181   0.264254  
3182   0.292814  

[3183 rows x 12 columns]

**Jaro-Winkler**

Took 8m53.0s on Louis' machine

In [185]:
jw_correction_df = get_correction_df(DATA_PATH + "\jw_correction_df.csv", typos, jellyfish.jaro_winkler_similarity, False, 5)
jw_correction_df

Word             Typo correction 0  correction 1  correction 2  \
0      wealthy         wealtohy      wealthy        wealth          weal   
1       afford            aford       afford        axford        alford   
2     Catholic  CatholiaCtholic        athol  palaeolithic  pathological   
3      cousins         coxusins      cousins        cousin      coxswain   
4        masks           mmasks        masks          mask          mass   
...        ...              ...          ...           ...           ...   
3178      keep            kpeep         keep          peep           kpe   
3179      game              gme          gme          gmes          game   
3180     winds          wantagh      wantagh       wantage          want   
3181      this              tsi          tsi          tsim          tsui   
3182        of                o          ose           ove           ovi   

     correction 3 correction 4  distance 0  distance 1  distance 2  \
0        wealthtv        welty    0.975000    0.950000    0.900000   
1            ford      affords    0.955556    0.950000    0.950000   
2       alghaithi         toit    0.777778    0.766667    0.766667   
3     compulsions         coun    0.966667    0.933333    0.883333   
4            asks          mma    0.950000    0.900000    0.900000   
...           ...          ...         ...         ...         ...   
3178        keeps          kee    0.940000    0.933333    0.906667   
3179         gome        gomer    1.000000    0.941667    0.925000   
3180         wang         wana    1.000000    0.942857    0.914286   
3181         tsai         tsoi    1.000000    0.941667    0.933333   
3182          oce          oft    0.800000    0.800000    0.800000   

      distance 3  distance 4  
0       0.900000    0.900000  
1       0.933333    0.923810  
2       0.765741    0.755556  
3       0.869697    0.866667  
4       0.888889    0.883333  
...          ...         ...  
3178    0.880000    0.880000  
3179    0.925000    0.880000  
3180    0.900000    0.900000  
3181    0.933333    0.933333  
3182    0.800000    0.800000  

[3183 rows x 12 columns]

In [186]:
jwUni_correction_df = get_weighted_numeric_correction_df(DATA_PATH + "\jwUni_correction_df.csv", typos, jellyfish.jaro_winkler_similarity, True, 5)
jwUni_correction_df

Word             Typo  correction 0 correction 1 correction 2  \
0      wealthy         wealtohy       healthy       wealth      wealthy   
1       afford            aford          ford       afford      watford   
2     Catholic  CatholiaCtholic  pathological         toit        athol   
3      cousins         coxusins        cousin      cousins     coursing   
4        masks           mmasks          mass         asks         mask   
...        ...              ...           ...          ...          ...   
3178      keep            kpeep          keep       upkeep         peep   
3179      game              gme          game         gome        gamel   
3180     winds          wantagh          want      wantage      wantagh   
3181      this              tsi           tsi         gtsi         tsoi   
3182        of                o           opt          ota          oco   

      correction 3 correction 4  distance 0  distance 1  distance 2  \
0         wealthtv         weal    0.552625    0.405552    0.001220   
1           alford       axford    0.544633    0.383306    0.007396   
2     palaeolithic    alghaithi    0.443006    0.226283    0.045403   
3             coun  compulsions    0.620832    0.301992    0.006891   
4            masks          mma    0.602861    0.152449    0.069508   
...            ...          ...         ...         ...         ...   
3178           kpe          kee    0.851026    0.079261    0.002756   
3179           gme         gmes    0.923628    0.000916    0.000221   
3180       wantage      wantagh    0.882370    0.029613    0.001040   
3181          tsim         tsoi    0.532955    0.201515    0.142045   
3182           ove          ose    0.610149    0.096318    0.067861   

      distance 3  distance 4  
0       0.000551    0.000334  
1       0.006585    0.000373  
2       0.030485    0.018787  
3       0.006695    0.005994  
4       0.068783    0.007964  
...          ...         ...  
3178    0.000821    0.000638  
3179    0.000155    0.000082  
3180    0.000615    0.000197  
3181    0.038790    0.027841  
3182    0.014925    0.010746  

[3183 rows x 12 columns]

Took 14m8.2s

In [187]:
jwSdx_correction_df = get_weighted_numeric_correction_df(DATA_PATH + "\jwSdx_correction_df.csv", typos, jellyfish.jaro_winkler_similarity, False, 5)
jwSdx_correction_df

Word             Typo  correction 0 correction 1  correction 2  \
0      wealthy         wealtohy       wealthy       wealth         welty   
1       afford            aford        afford      affords        axford   
2     Catholic  CatholiaCtholic  pathological        athol  palaeolithic   
3      cousins         coxusins       cousins       cousin      coxswain   
4        masks           mmasks         masks         mask          mass   
...        ...              ...           ...          ...           ...   
3178      keep            kpeep          keep          kpe         keeps   
3179      game              gme           gme         game          gome   
3180     winds          wantagh       wantagh      wantage          want   
3181      this              tsi           tsi         tsui          tsai   
3182        of                o           ose          ove           ovi   

     correction 3 correction 4  distance 0  distance 1  distance 2  \
0            weal     wealthtv    0.975000    0.950000    0.900000   
1          alford         ford    0.955556    0.923810    0.678571   
2       alghaithi         toit    0.702778    0.648148    0.575000   
3     compulsions         coun    0.805556    0.777778    0.736111   
4            asks          mma    0.950000    0.900000    0.900000   
...           ...          ...         ...         ...         ...   
3178         peep          kee    0.805714    0.777143    0.754286   
3179         gmes        gomer    1.000000    0.925000    0.925000   
3180         wang         wana    1.000000    0.942857    0.731429   
3181         tsoi         tsim    1.000000    0.933333    0.933333   
3182          oce          oft    0.666667    0.666667    0.666667   

      distance 3  distance 4  
0       0.450000    0.450000  
1       0.678571    0.533333  
2       0.574306    0.566667  
3       0.652273    0.650000  
4       0.444444    0.441667  
...          ...         ...  
3178    0.666667    0.628571  
3179    0.470833    0.440000  
3180    0.540000    0.540000  
3181    0.933333    0.000000  
3182    0.666667    0.533333  

[3183 rows x 12 columns]

In [243]:
jwCmp_correction_df = get_composite_numeric_correction_df(DATA_PATH + "\jwCmp_correction_df.csv", typos, jellyfish.jaro_winkler_similarity, 0.5, 5)
jwCmp_correction_df

Correcting Typos:   0%|          | 0/3183 [00:00<?, ?it/s]C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:74: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["soundex"] = 1 - soundex / np.sum(soundex)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:77: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_words["weight"] = top_words["words"].apply(unigram_weighing)
C:\Users\Louis\AppData\Local\Temp\ipykernel_10200\2668738701.py:78: SettingWithCopyWarning: 
A value is tryi

KeyboardInterrupt: 

**Edit Distance**

Took 19m10.3s on Louis' machine

In [188]:
ed_correction_df = get_correction_df(DATA_PATH + "\ed_correction_df.csv", typos, editdistance.eval, True, 5)
ed_correction_df

Word             Typo    correction 0 correction 1 correction 2  \
0      wealthy         wealtohy         wealthy       wealth      healthy   
1       afford            aford          alford         ford       afford   
2     Catholic  CatholiaCtholic  anglo-catholic  paleolithic   pathologic   
3      cousins         coxusins         cousins       cousin      commins   
4        masks           mmasks           masks        amass        marks   
...        ...              ...             ...          ...          ...   
3178      keep            kpeep            peep         keep         meep   
3179      game              gme             gme          ime          gue   
3180     winds          wantagh         wantagh      wantage      wastage   
3181      this              tsi             tsi          asi          tti   
3182        of                o             oli          bom          wto   

       correction 3     correction 4  distance 0  distance 1  distance 2  \
0             welty          healton           1           2           2   
1            axford            acord           1           1           1   
2     anti-catholic  catholic-muslim           7           7           7   
3          focusing           coulis           1           2           3   
4             tasks            masts           1           2           2   
...             ...              ...         ...         ...         ...   
3178           reep            koepp           1           1           2   
3179            bme              gfe           0           1           1   
3180        vantage          wattage           0           1           2   
3181            tst              tsk           0           1           1   
3182            otc              dpo           2           2           2   

      distance 3  distance 4  
0              3           3  
1              1           1  
2              7           7  
3              3           3  
4              2           2  
...          ...         ...  
3178           2           2  
3179           1           1  
3180           2           2  
3181           1           1  
3182           2           2  

[3183 rows x 12 columns]

Took 26m8.1s

In [189]:
edUni_correction_df = get_weighted_ed_correction_df(DATA_PATH + "\edUni_correction_df.csv", typos, True, 5)
edUni_correction_df

Word             Typo correction 0   correction 1 correction 2  \
0      wealthy         wealtohy      wealthy        healthy       wealth   
1       afford            aford         ford         afford       alford   
2     Catholic  CatholiaCtholic   shopaholic  anti-catholic  paleolithic   
3      cousins         coxusins      cousins         cousin      housing   
4        masks           mmasks        masks           mass        marks   
...        ...              ...          ...            ...          ...   
3178      keep            kpeep         keep           peep         deep   
3179      game              gme          gme           game          gmt   
3180     winds          wantagh      wantagh        wantage      vantage   
3181      this              tsi          tsi            tsb          tsa   
3182        of                o          for            not          who   

        correction 3     correction 4      weight 0      weight 1  \
0             health           walton  3.579388e-05  7.064333e-05   
1              acord            afore  8.378619e-05  5.759642e-05   
2     anglo-catholic  catholic-muslim  4.232956e-07  3.668562e-07   
3            causing         contains  7.760419e-06  1.652358e-05   
4               asks            tasks  1.021365e-05  9.449275e-05   
...              ...              ...           ...           ...   
3178           speed             knee  3.385330e-04  1.104331e-06   
3179             gmc              gee  9.030306e-08  5.825300e-04   
3180         wastage          wattage  1.015909e-07  3.367552e-07   
3181             tsx              csi  1.881314e-07  6.962742e-06   
3182             one              you  1.272489e-02  4.346704e-03   

          weight 2      weight 3      weight 4  
0     5.005800e-05  6.505978e-04  5.446403e-06  
1     9.952150e-07  9.594700e-08  5.643941e-08  
2     1.900127e-07  1.617930e-07  8.654043e-08  
3     1.679675e-04  6.213603e-05  3.141041e-05  
4     4.663965e-05  2.419369e-05  1.335733e-05  
...            ...           ...           ...  
3178  1.079329e-04  8.427533e-05  5.586937e-05  
3179  8.266681e-05  4.300683e-06  3.361908e-06  
3180  2.987526e-06  6.415280e-07  4.910229e-07  
3181  6.232792e-06  3.753221e-06  3.725001e-06  
3182  3.967360e-03  2.748979e-03  2.485445e-03  

[3183 rows x 12 columns]

Took 15m50.9s

In [190]:
edSdx_correction_df = get_weighted_ed_correction_df(DATA_PATH + "\edSdx_correction_df.csv", typos, False, 5)
edSdx_correction_df

Word             Typo     correction 0 correction 1 correction 2  \
0      wealthy         wealtohy          wealthy       wealth      healthy   
1       afford            aford           afford        acord       alford   
2     Catholic  CatholiaCtholic  catholic-muslim   pathologic  paleolithic   
3      cousins         coxusins          cousins       cousin     focusing   
4        masks           mmasks            masks        tasks        marks   
...        ...              ...              ...          ...          ...   
3178      keep            kpeep             keep         peep        koepp   
3179      game              gme              gme          ime          gue   
3180     winds          wantagh          wantagh      wantage      wastage   
3181      this              tsi              tsi          tsk          asi   
3182        of                o              oli          bom          wto   

       correction 3    correction 4  weight 0  weight 1  weight 2  weight 3  \
0             welty         healton         0         0         1         0   
1            axford            ford         0         1         2         2   
2     anti-catholic  anglo-catholic         0         1         3         3   
3            coulis         commins         2         2         1         2   
4             masts           amass         0         1         2         2   
...             ...             ...       ...       ...       ...       ...   
3178           meep            reep         1         2         1         2   
3179            bme             gfe         0         1         1         1   
3180        vantage         wattage         0         0         1         1   
3181            tti             tst         0         0         1         1   
3182            otc             dpo         1         2         2         2   

      weight 4  
0            2  
1            3  
2            4  
3            3  
4            3  
...        ...  
3178         2  
3179         1  
3180         2  
3181         1  
3182         2  

[3183 rows x 12 columns]

In [ ]:
edCmp_correction_df = get_composite_ed_correction_df(DATA_PATH + "\edCmp_correction_df.csv", typos, 0.5, 5)
edCmp_correction_df

## 1.4 Return the text file with the corrections 

### 1.4.1 Functions

In [191]:
def format_correction(typo_row):
    name = typo_row["Word"]
    typo = typo_row['Typo']
    
    #print(typo_row)
    
    neigh0 = typo_row["correction 0"]
    neigh1 = typo_row["correction 1"]
    neigh2 = typo_row["correction 2"]
    neigh3 = typo_row["correction 3"]
    neigh4 = typo_row["correction 4"]
    return f"<correction orig=\"{name}\" typo=\"{typo}\">{neigh0} {neigh1} {neigh2} {neigh3} {neigh4}</correction>"

def format_typo(typo_row):
    orig = typo_row["Word"]
    typo = typo_row['Typo']
    return f'<typo orig="{orig}">{typo}</typo>'

def replace_typos(path, typo_df, typos_str): 
 
    formatted_corr = typo_df.apply(format_correction, axis=1)
    formatted_typo = typo_df.apply(format_typo, axis=1)

    formatted_dict = dict(zip(formatted_typo, formatted_corr))

    # Erase the contents of the file if it already exists
    if os.path.isfile(path):
        os.remove(path)

    for typo_pattern in formatted_dict.keys():
        correction_pattern = formatted_dict[typo_pattern]
        typos_str = re.sub(typo_pattern, correction_pattern, typos_str)

    # Write it to a .txt file
    with open(path, "a", encoding="utf-8") as out_file:
        out_file.write(typos_str)

### 1.4.2 Replace typos for all distances

In [192]:
typos_file = open(DATA_PATH + r"\typo-0.2.txt").read()

**Jaro**

In [246]:
jaroCmp_correction_df

Word             Typo  correction 0 correction 1 correction 2  \
0      wealthy         wealtohy        wealth      wealthy      healthy   
1       afford            aford        afford         ford       alford   
2     Catholic  CatholiaCtholic  pathological         toit        athol   
3      cousins         coxusins        cousin      cousins     coursing   
4        masks           mmasks          mass        masks         mask   
...        ...              ...           ...          ...          ...   
3178      keep            kpeep          keep          kpe         peep   
3179      game              gme          game          gme         gome   
3180     winds          wantagh          want      wantagh      wantage   
3181      this              tsi           tsi         tsoi         tasi   
3182        of                o           opt          ota          oco   

      correction 3 correction 4 distance 0 distance 1 distance 2 distance 3  \
0            welty       watley   0.604697   0.588581   0.485506   0.437826   
1           axford      watford   0.658032   0.593786   0.380988    0.37796   
2     palaeolithic    alghaithi   0.572892   0.396475   0.346776   0.302743   
3         coxswain  compulsions   0.664722    0.52968   0.387464   0.336511   
4             asks      unmasks   0.744777   0.506714   0.479072    0.41023   
...            ...          ...        ...        ...        ...        ...   
3178         peeps       upkeep   0.876489   0.385614   0.364469   0.337807   
3179          gmes        gamel   0.915971   0.500077   0.458787   0.229207   
3180          anta         wata   0.785263   0.500102   0.452686    0.28575   
3181          gtsi         atsi   0.739234   0.504386   0.497807   0.347588   
3182           ofs          otv   0.654588   0.356442   0.346118   0.294482   

     distance 4  
0      0.143911  
1      0.328853  
2      0.296546  
3      0.295813  
4      0.106271  
...         ...  
3178   0.294658  
3179   0.216791  
3180   0.214325  
3181   0.264254  
3182   0.292814  

[3183 rows x 12 columns]

In [245]:
replace_typos(DATA_PATH + "\jaro_corrections-0.2.txt", jaro_correction_df, typos_file)
replace_typos(DATA_PATH + "\jaroUni_corrections-0.2.txt", jaroUni_correction_df, typos_file)
replace_typos(DATA_PATH + "\jaroSdx_corrections-0.2.txt", jaroSdx_correction_df, typos_file)
replace_typos(DATA_PATH + "\jaroCmp_corrections-0.2.txt", jaroCmp_correction_df, typos_file)

**Jaro-Winkler**

In [194]:
replace_typos(DATA_PATH + "\jw_corrections-0.2.txt", jw_correction_df, typos_file)
replace_typos(DATA_PATH + "\jwUni_corrections-0.2.txt", jwUni_correction_df, typos_file)
replace_typos(DATA_PATH + "\jwSdx_corrections-0.2.txt", jwSdx_correction_df, typos_file)

**Edit Distance**

In [195]:
replace_typos(DATA_PATH + "\ed_corrections-0.2.txt", ed_correction_df, typos_file)
replace_typos(DATA_PATH + "\edUni_corrections-0.2.txt", edUni_correction_df, typos_file)
replace_typos(DATA_PATH + "\edSdx_corrections-0.2.txt", edSdx_correction_df, typos_file)

# 2. Create evaluation metrics
Here's a couple of ideas:

- *Hard* accuracy: Does the first word match the original word?
- *Soft* accuracy: Is the original word in one of the neighbors? 

In [196]:
def evaluate_correction(path):
    corrected_file = open(path).read()
    correction_pattern = r'<correction.*?</correction>'
    matches = re.findall(correction_pattern, corrected_file)

    hardacc = []
    softacc = []
    extraction_pattern = '<correction orig="|" typo="|">|</correction>'
    for correction in matches: 
        subbed_corr = re.sub(extraction_pattern, " ", correction) # Remove all the fluff
        extracted_words = subbed_corr.split(" ")[1:-1] # remove the frst and last splits, which will always be empty

        original = extracted_words[0] 
        corrected = extracted_words[2:]

        hardacc.append(original == corrected[0])
        softacc.append(original in corrected)

    hard_accuracy = sum(hardacc) / len(hardacc)
    soft_accuracy = sum(softacc) / len(softacc)

    print(f"Hard accuracy: {round(hard_accuracy, 2)}\nSoft accuracy: {round(soft_accuracy, 2)}")
        
    return hard_accuracy, soft_accuracy

**Jaro**

In [247]:
print("Regular Jaro:")
corr_path = DATA_PATH + r"\jaro_corrections-0.2.txt"
evaluate_correction(corr_path)
print("\nJaro with Unigram weighing:")
corr_path = DATA_PATH + r"\jaroUni_corrections-0.2.txt"
evaluate_correction(corr_path)
print("\nJaro with Soundex Weighing:")
corr_path = DATA_PATH + r"\jaroSdx_corrections-0.2.txt"
evaluate_correction(corr_path)
print("\nJaro with Composite Weighing:")
corr_path = DATA_PATH + r"\jaroCmp_corrections-0.2.txt"
evaluate_correction(corr_path)

Regular Jaro:
Hard accuracy: 0.29
Soft accuracy: 0.44

Jaro with Unigram weighing:
Hard accuracy: 0.35
Soft accuracy: 0.44

Jaro with Soundex Weighing:
Hard accuracy: 0.27
Soft accuracy: 0.44

Jaro with Composite Weighing:
Hard accuracy: 0.36
Soft accuracy: 0.44


(0.3595080416272469, 0.43550930305897195)

**Jaro-Winkler**

In [200]:
print("Regular JW:")
corr_path = DATA_PATH + r"\jw_corrections-0.2.txt"
evaluate_correction(corr_path)
print("\nJW with Unigram weighing:")
corr_path = DATA_PATH + r"\jwUni_corrections-0.2.txt"
evaluate_correction(corr_path)
print("\nJW with Soundex Weighing:")
corr_path = DATA_PATH + r"\jwSdx_corrections-0.2.txt"
evaluate_correction(corr_path)

Regular JW:
Hard accuracy: 0.28
Soft accuracy: 0.44

JW with Unigram weighing:
Hard accuracy: 0.35
Soft accuracy: 0.44

JW with Soundex Weighing:
Hard accuracy: 0.25
Soft accuracy: 0.44


(0.2532324187953327, 0.4374014506464838)

**Edit Distance**

In [201]:
print("Regular ED:")
corr_path = DATA_PATH + r"\ed_corrections-0.2.txt"
evaluate_correction(corr_path)
print("\nED with Unigram weighing:")
corr_path = DATA_PATH + r"\edUni_corrections-0.2.txt"
evaluate_correction(corr_path)
print("\nED with Soundex Weighing:")
corr_path = DATA_PATH + r"\edSdx_corrections-0.2.txt"
evaluate_correction(corr_path)

Regular ED:
Hard accuracy: 0.24
Soft accuracy: 0.38

ED with Unigram weighing:
Hard accuracy: 0.37
Soft accuracy: 0.52

ED with Soundex Weighing:
Hard accuracy: 0.26
Soft accuracy: 0.38


(0.25953957742037215, 0.3781141595711132)